Тут я использовал gensom версии 3.6.1, так что в процессе могут появиться какие-то warnings

In [18]:
%load_ext autoreload

from gensim.models import Word2Vec, KeyedVectors

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [2]:
import csv
import pymorphy2
import string
import re
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
from scipy import spatial

morph = pymorphy2.MorphAnalyzer()

In [3]:
def get_texts():
    corpus = []
    inquiery = []
    scores = []
    normal = []

    with open('quora_question_pairs_rus.csv', encoding = 'utf-8') as csvfile:
        readCSV = csv.reader(csvfile, delimiter=',')
        for row in readCSV:
            normal.append(row[2])
            text = preproc(row[2])
            corpus.append(text)
            inquiery.append(row[1])
            #lenghths.append(len(text.split(' ')))
            scores.append(row[3])
            if len(scores) == 20000:
                #return [corpus, inquiery, lenghths, scores, normal]
                return [corpus, inquiery, scores, normal]

def preproc(data):                      # препроцессинг (убираем знаки препинания и числа, приводим всё к начальной форме)
            data = data.split()        
            text = ''                   # числа есть только в тех информации, в самом скрипте все числа пишутся буквами
            for word in data:
                word = word.strip('[!,.?"]')
                p = morph.parse(word.strip())[0]
                p = p.normal_form
                if p != '-':
                    if re.search(r'\d', p) == None:
                        text  = text + ' ' + p
            return text[1:]    

In [4]:
data = get_texts()

In [5]:
corpus_texts, inquiery_texts, scores, normal_texts =  data[0][1:], data[1][1:], data[2][1:], data[3][1:]
del data

In [6]:
print(corpus_texts[1])
print(inquiery_texts[1])
print(scores[1])

как повысить скорость интернет путём взлом через dns
как я могу увеличить скорость моего интернет-соединения, используя vpn
0


In [7]:
#тут нужны данные
model_file = './fast/model.model'

In [8]:
model = KeyedVectors.load(model_file)

C:\Users\asus\Anaconda3\lib\site-packages\smart_open\smart_open_lib.py:398: UserWarning: This function is deprecated, use smart_open.open instead. See the migration notes for details: https://github.com/RaRe-Technologies/smart_open/blob/master/README.rst#migrating-to-the-new-open-function
  'See the migration notes for details: %s' % _MIGRATION_NOTES_URL


In [9]:
model.wv

C:\Users\asus\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  """Entry point for launching an IPython kernel.


In [10]:
lemma = 'черепаха'
lemma in model.wv.vocab

C:\Users\asus\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  


True

In [11]:
model.vector_size

300

In [12]:
vecs = []
for text in corpus_texts:
    lenghth = 0
    res = np.zeros((model.vector_size,), dtype = 'float32')
    for word in text.split(' '):
        if word in model.wv.vocab:
            lenghth += 1
            res += model.wv[word]
    res = res/lenghth
    vecs.append(res)

C:\Users\asus\Anaconda3\lib\site-packages\ipykernel_launcher.py:6: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  
C:\Users\asus\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  
C:\Users\asus\Anaconda3\lib\site-packages\ipykernel_launcher.py:9: RuntimeWarning: invalid value encountered in true_divide
  if __name__ == '__main__':


In [13]:
vecs

[array([ 1.61135867e-01,  6.41763583e-02,  2.36377612e-01,  4.90588844e-02,
        -4.75962239e-04,  6.65353313e-02,  2.30170358e-02, -1.48942515e-01,
        -3.16009782e-02,  7.91569427e-02, -2.58823782e-01,  5.64404726e-02,
         1.60538033e-01, -3.62385750e-01,  1.32908732e-01,  1.75583571e-01,
        -4.41870205e-02, -3.46157812e-02, -8.28663111e-02, -2.77089719e-02,
        -1.63666517e-01,  1.48551002e-01, -1.03624068e-01, -1.77825421e-01,
        -7.48570934e-02,  1.26576558e-01,  6.34605885e-02, -3.11995540e-02,
        -7.66464248e-02,  8.82132724e-02, -7.84251094e-02, -1.75509322e-02,
         2.46380866e-02,  6.71849027e-02, -1.32332206e-01, -1.10742286e-01,
         1.22207507e-01, -1.11688310e-02,  4.41127308e-02, -9.95755289e-03,
         5.19873276e-02, -3.47027510e-01,  2.05473527e-01,  1.10743299e-01,
        -6.88284785e-02, -2.32833952e-01, -2.47984126e-01,  1.05183080e-01,
        -4.59535792e-02,  1.29276365e-02, -2.06260756e-01,  1.18764617e-01,
        -2.5

In [14]:
vecz = np.nan_to_num(vecs)

In [15]:
def inquiery_vector(inq ):
    inq_vec = np.zeros((model.vector_size,), dtype = 'float32')
    inq_l = 0
    for word in preproc(inq).split():
        if word in model.wv.vocab:
            inq_l += 1
            inq_vec += model.wv[word]
    inq_vec = inq_vec/lenghth
    return inq_vec

In [16]:
def search_fasttext(inq):
    
    inq_vec = inquiery_vector(inq).reshape(-1,1)
    results = {}
    for index, text in enumerate(vecz):
        a = text.reshape(-1,1)
        res = 1 - spatial.distance.cosine(a, inq_vec )
        results[index] = res
    r = sorted(results, key=results.get, reverse=True)[:5]
    for i in r:
        print(normal_texts[i])
    return 

In [17]:
search_fasttext('правительство индии')

C:\Users\asus\Anaconda3\lib\site-packages\ipykernel_launcher.py:5: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  """
C:\Users\asus\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  import sys
C:\Users\asus\Anaconda3\lib\site-packages\scipy\spatial\distance.py:702: RuntimeWarning: invalid value encountered in float_scalars
  dist = 1.0 - uv / np.sqrt(uu * vv)


какая разница между парламентом и правительством Индии
может нарэндра modi стать премьер-министром Индии в 2019 году
это решение правительства Индии запретить 500 и 1000 рупий отмечает мастер-ход или ошибочный план
что, если Индия и Китай урегулируют свои споры и объединиться
почему мусульманские правители Индии не инвестировали в создание университетов на субконтиненте


# оценка качества

судя по эому результату, он лажает посильнее bm25, тут проверяем качество.

In [ ]:
def search_fasttext_q(inq):
    
    inq_vec = inquiery_vector(inq).reshape(-1,1)
    results = {}
    for index, text in enumerate(vecz):
        a = text.reshape(-1,1)
        res = 1 - spatial.distance.cosine(a, inq_vec )
        results[index] = res
    r = sorted(results, key=results.get, reverse=True)[:5]
    return r

In [ ]:
d ={}
for i in range(1000):
    if int(scores[i]) == 1:
        if inquiery_texts[i] in d.keys():
            d[inquiery_texts[i]].append(normal_texts[i])
        else:
            d[inquiery_texts[i]] = [normal_texts[i]]

In [ ]:
count = 0
for i in range(1000):
    print(i)
    res = search_np(inquiery_texts[i], N, voc)
    c = 0
    if  inquiery_texts[i] in d.keys():
        for j in res:
            if normal_texts[j] in d[inquiery_texts[i]]:
                c = 1
    count += c
    
print((count/N)*100)

In [24]:
modele_file = './elmo/model.hdf5'

In [ ]:
import pandas

In [42]:
modele = Word2Vec.load(modele_file)

UnpicklingError: invalid load key, 'H'.

In [18]:
inq_vec = inquiery_vector('правительство индии')
b = inq_vec.reshape(-1,1)
a = vecs[1].reshape(-1,1)
from scipy import spatial

result = spatial.distance.cosine(a,b )

C:\Users\asus\Anaconda3\lib\site-packages\ipykernel_launcher.py:5: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  """
C:\Users\asus\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  import sys


In [19]:
result

0.6468781530857086

In [84]:
np.where(np.isnan(vecs))

(array([ 2613,  2613,  2613, ..., 15685, 15685, 15685], dtype=int64),
 array([  0,   1,   2, ..., 297, 298, 299], dtype=int64))

ValueError: The truth value of an array with more than one element is ambiguous. Use a.any() or a.all()